In [2]:
from transformers import DistilBertTokenizer
from transformers import TFDistilBertForSequenceClassification
import tensorflow as tf
import pandas as pd
import json
import gc

In [25]:
df = pd.read_csv('train_data.csv')
df.head()

category                                               text
0  Technical writer  organize material and complete writing assignm...
1  Technical writer   maintain records and files of work and revisions
2  Technical writer  edit  standardize  or make changes to material...
3  Technical writer  select photographs  drawings  sketches  diagra...
4  Technical writer  interview production and engineering personnel...

In [26]:
df['encoded_cat'] = df['category'].astype('category').cat.codes
df.head()

category                                               text  \
0  Technical writer  organize material and complete writing assignm...   
1  Technical writer   maintain records and files of work and revisions   
2  Technical writer  edit  standardize  or make changes to material...   
3  Technical writer  select photographs  drawings  sketches  diagra...   
4  Technical writer  interview production and engineering personnel...   

   encoded_cat  
0           55  
1           55  
2           55  
3           55  
4           55

In [5]:
data_texts = df["text"].to_list() # Features (not-tokenized yet)
data_labels = df["encoded_cat"].to_list() # Lables

In [6]:
from sklearn.model_selection import train_test_split

# Split Train and Validation data
train_texts, val_texts, train_labels, val_labels = train_test_split(data_texts, data_labels, test_size=0.2, random_state=1000)

In [7]:
tokenizer = DistilBertTokenizer.from_pretrained('distilbert-base-uncased')
train_encodings = tokenizer(train_texts, truncation=True, padding=True)
val_encodings = tokenizer(val_texts, truncation=True, padding=True)

In [8]:
train_dataset = tf.data.Dataset.from_tensor_slices((
    dict(train_encodings),
    train_labels
))
val_dataset = tf.data.Dataset.from_tensor_slices((dict(val_encodings), val_labels ))

In [9]:
model = TFDistilBertForSequenceClassification.from_pretrained('distilbert-base-uncased', num_labels=21)

optimizer = tf.keras.optimizers.Adam(learning_rate=5e-5)
model.compile(optimizer=optimizer, loss=model.compute_loss, metrics=['accuracy'])

Some layers from the model checkpoint at distilbert-base-uncased were not used when initializing TFDistilBertForSequenceClassification: ['vocab_transform', 'activation_13', 'vocab_projector', 'vocab_layer_norm']
- This IS expected if you are initializing TFDistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some layers of TFDistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['dropout_19', 'pre_classifier', 'classifier']
You should probably TRAIN this model on a down-stream task to be able to use i

In [11]:
model.fit(train_dataset.shuffle(100).batch(16), epochs=5, batch_size=16, validation_data=val_dataset.shuffle(100).batch(16))

Epoch 1/5
62/62 [==============================] - 8s 123ms/step - loss: 1.5237 - accuracy: 0.5237 - val_loss: 2.2847 - val_accuracy: 0.3024
Epoch 2/5
62/62 [==============================] - 7s 105ms/step - loss: 1.4421 - accuracy: 0.5378 - val_loss: 2.3720 - val_accuracy: 0.2823
Epoch 3/5
62/62 [==============================] - 7s 106ms/step - loss: 1.3973 - accuracy: 0.5439 - val_loss: 2.4879 - val_accuracy: 0.2742
Epoch 4/5
62/62 [==============================] - 7s 105ms/step - loss: 1.3523 - accuracy: 0.5610 - val_loss: 2.4525 - val_accuracy: 0.2944
Epoch 5/5
62/62 [==============================] - 7s 111ms/step - loss: 1.3322 - accuracy: 0.5469 - val_loss: 2.5269 - val_accuracy: 0.2944


In [12]:
save_directory = "/saved_models" # change this to your preferred location

model.save_pretrained(save_directory)
tokenizer.save_pretrained(save_directory)

('/saved_models/tokenizer_config.json',
 '/saved_models/special_tokens_map.json',
 '/saved_models/vocab.txt',
 '/saved_models/added_tokens.json')

In [13]:
loaded_tokenizer = DistilBertTokenizer.from_pretrained(save_directory)
loaded_model = TFDistilBertForSequenceClassification.from_pretrained(save_directory)

Some layers from the model checkpoint at /saved_models were not used when initializing TFDistilBertForSequenceClassification: ['dropout_19']
- This IS expected if you are initializing TFDistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some layers of TFDistilBertForSequenceClassification were not initialized from the model checkpoint at /saved_models and are newly initialized: ['dropout_39']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [17]:
!pip install huggingface_hub

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [18]:

from huggingface_hub import notebook_login

notebook_login()

Token is valid.
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.cache/huggingface/token
Login successful


In [20]:
model.push_to_hub("lfernandopg/Proyecto-Transformers")

tf_model.h5:   0%|          | 0.00/268M [00:00<?, ?B/s]

Upload 1 LFS files:   0%|          | 0/1 [00:00<?, ?it/s]

In [24]:
tokenizer.push_to_hub("lfernandopg/Proyecto-Transformers")

CommitInfo(commit_url='https://huggingface.co/lfernandopg/Proyecto-Transformers/commit/609ec9a9f028cf40873cd1180aa1776bdb0126b9', commit_message='Upload tokenizer', commit_description='', oid='609ec9a9f028cf40873cd1180aa1776bdb0126b9', pr_url=None, pr_revision=None, pr_num=None)